# Домашнее задание к лекции "Основы веб-скрапинга и работы с API"
Задание 1.
Обязательная часть
Будем парсить страницу со свежеми новостям на habr.com/ru/all/.

Вам необходимо собирать только те статьи, в которых встречается хотя бы одно требуемое ключевое слово. Эти слова определяем в начале кода в переменной, например:

KEYWORDS = ['python', 'парсинг']

Поиск вести по всей доступной preview-информации (это информация, доступная непосредственно с текущей страницы).

В итоге должен формироваться датафрейм вида: <дата> - <заголовок> - <ссылка>

Дополнительная часть (необязательная)
Улучшить скрипт так, чтобы он анализировал не только preview-информацию статьи, но и весь текст статьи целиком.

Для этого потребуется получать страницы статей и искать по тексту внутри этой страницы.

Итоговый датафрейм формировать со столбцами: <дата> - <заголовок> - <ссылка> - <текст_статьи>

In [129]:
import pandas as pd
from bs4 import BeautifulSoup
import requests
import time
url = 'https://habr.com/ru/all/'
KEYWORDS = ['python', 'парсинг']
#params = {    'search_query': 'python'}

In [130]:
req = requests.get('https://habr.com/ru/all/')
soup = BeautifulSoup(req.text, 'html.parser')
soup

<!DOCTYPE html>

<html data-vue-meta="%7B%22lang%22:%7B%22ssr%22:%22ru%22%7D%7D" lang="ru">
<head>
<meta charset="utf-8"/>
<meta content="width=device-width,initial-scale=1.0,viewport-fit=cover" name="viewport"/>
<title>Все публикации подряд / Хабр</title>
<style>
    /* cyrillic-ext */
    @font-face {
      font-family: 'Fira Sans';
      font-style: normal;
      font-weight: 500;
      font-display: swap;
      src: url(https://fonts.gstatic.com/s/firasans/v11/va9B4kDNxMZdWfMOD5VnZKveSxf6TF0.woff2) format('woff2');
      unicode-range: U+0460-052F, U+1C80-1C88, U+20B4, U+2DE0-2DFF, U+A640-A69F, U+FE2E-FE2F;
    }

    /* cyrillic */
    @font-face {
      font-family: 'Fira Sans';
      font-style: normal;
      font-weight: 500;
      font-display: swap;
      src: url(https://fonts.gstatic.com/s/firasans/v11/va9B4kDNxMZdWfMOD5VnZKveQhf6TF0.woff2) format('woff2');
      unicode-range: U+0400-045F, U+0490-0491, U+04B0-04B1, U+2116;
    }

    /* latin-ext */
    @font-face {
      

In [131]:
#news_blocks = soup.find_all('a', class_='post__title_link')
news_blocks = soup.find_all('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2')
news_blocks


[<h2 class="tm-article-snippet__title tm-article-snippet__title_h2"><a class="tm-article-snippet__title-link" data-article-link="" href="/ru/post/571976/"><span>Танцующие горы Ирана по данным спутниковой интерферометрии</span></a></h2>,
 <h2 class="tm-article-snippet__title tm-article-snippet__title_h2"><a class="tm-article-snippet__title-link" data-article-link="" href="/ru/company/postgrespro/blog/568662/"><span>Postgresso 33</span></a></h2>,
 <h2 class="tm-article-snippet__title tm-article-snippet__title_h2"><a class="tm-article-snippet__title-link" data-article-link="" href="/ru/post/571974/"><span>Важные советы от HR специалиста для тех, кто готовится к собеседованию</span></a></h2>,
 <h2 class="tm-article-snippet__title tm-article-snippet__title_h2"><a class="tm-article-snippet__title-link" data-article-link="" href="/ru/company/ruvds/blog/569694/"><span>Восстановление 4-летнего автомобильного AGM аккумулятора</span></a></h2>,
 <h2 class="tm-article-snippet__title tm-article-snip

In [132]:
a_list = list(map(lambda x: x.find('a').get('href'), news_blocks))
a_list

['/ru/post/571976/',
 '/ru/company/postgrespro/blog/568662/',
 '/ru/post/571974/',
 '/ru/company/ruvds/blog/569694/',
 '/ru/post/571810/',
 '/ru/post/571964/',
 '/ru/company/JetBrains/blog/571962/',
 '/ru/post/571956/',
 '/ru/post/571954/',
 '/ru/company/bizone/blog/571512/',
 '/ru/post/571950/',
 '/ru/company/group-ib/blog/571940/',
 '/ru/company/cloud4y/blog/571942/',
 '/ru/post/571944/',
 '/ru/company/netcracker/blog/571934/',
 '/ru/post/571786/',
 '/ru/post/571930/',
 '/ru/company/accenture/blog/571918/',
 '/ru/company/pvs-studio/blog/571926/',
 '/ru/company/infoculture/blog/571924/']

In [133]:
all_refs = list(map(lambda x: 'https://habr.com/ru/all' + x, a_list))
all_refs

['https://habr.com/ru/all/ru/post/571976/',
 'https://habr.com/ru/all/ru/company/postgrespro/blog/568662/',
 'https://habr.com/ru/all/ru/post/571974/',
 'https://habr.com/ru/all/ru/company/ruvds/blog/569694/',
 'https://habr.com/ru/all/ru/post/571810/',
 'https://habr.com/ru/all/ru/post/571964/',
 'https://habr.com/ru/all/ru/company/JetBrains/blog/571962/',
 'https://habr.com/ru/all/ru/post/571956/',
 'https://habr.com/ru/all/ru/post/571954/',
 'https://habr.com/ru/all/ru/company/bizone/blog/571512/',
 'https://habr.com/ru/all/ru/post/571950/',
 'https://habr.com/ru/all/ru/company/group-ib/blog/571940/',
 'https://habr.com/ru/all/ru/company/cloud4y/blog/571942/',
 'https://habr.com/ru/all/ru/post/571944/',
 'https://habr.com/ru/all/ru/company/netcracker/blog/571934/',
 'https://habr.com/ru/all/ru/post/571786/',
 'https://habr.com/ru/all/ru/post/571930/',
 'https://habr.com/ru/all/ru/company/accenture/blog/571918/',
 'https://habr.com/ru/all/ru/company/pvs-studio/blog/571926/',
 'https:

In [125]:
# объединим все в одну функцию
def get_all_links(url, query, pages):
    all_refs = []
    params = {
        'search_query': query,
    }
    for i in range(1, pages):
        params['page'] = i
        res = requests.get(url, params)
        time.sleep(0.3)
        soup = BeautifulSoup(res.text, 'html.parser')
        news_blocks = soup.find_all('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2')
        a_list = list(map(lambda x: x.find('a').get('href'), news_blocks))
        all_refs += list(map(lambda x: 'https://habr.com' + x, a_list))
    return all_refs

all_links = get_all_links(url, KEYWORDS, 10)
all_links

['https://habr.com/ru/post/571976/',
 'https://habr.com/ru/company/postgrespro/blog/568662/',
 'https://habr.com/ru/post/571974/',
 'https://habr.com/ru/company/ruvds/blog/569694/',
 'https://habr.com/ru/post/571810/',
 'https://habr.com/ru/post/571964/',
 'https://habr.com/ru/company/JetBrains/blog/571962/',
 'https://habr.com/ru/post/571956/',
 'https://habr.com/ru/post/571954/',
 'https://habr.com/ru/company/bizone/blog/571512/',
 'https://habr.com/ru/post/571950/',
 'https://habr.com/ru/company/group-ib/blog/571940/',
 'https://habr.com/ru/company/cloud4y/blog/571942/',
 'https://habr.com/ru/post/571944/',
 'https://habr.com/ru/company/netcracker/blog/571934/',
 'https://habr.com/ru/post/571786/',
 'https://habr.com/ru/post/571930/',
 'https://habr.com/ru/company/accenture/blog/571918/',
 'https://habr.com/ru/company/pvs-studio/blog/571926/',
 'https://habr.com/ru/company/infoculture/blog/571924/',
 'https://habr.com/ru/post/571976/',
 'https://habr.com/ru/company/postgrespro/blog/

In [134]:
for link in all_links:
    soup = BeautifulSoup(requests.get(link).text, 'html.parser')
    time.sleep(0.2)

    if soup.find('span', class_='tm-article-snippet__datetime-published'):
        date = pd.to_datetime(soup.find('span', class_='tm-article-snippet__datetime-published').find('time').get('datetime'), dayfirst=True).date()
    elif soup.find('div', class_='tm-news-block__meta'):
        date = pd.to_datetime(soup.find('div', class_='tm-news-block__meta').find('time').get('datetime'), dayfirst=True).date()
    print(date)
    if soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2'): 
        title = soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2').text
    elif soup.find('h3', class_='tm-news-block__title'):
        title = soup.find('h3', class_='tm-news-block__title').text
    else:
        title = soup.find('h1', class_='tm-article-snippet__title tm-article-snippet__title_h1').text
    print(title)
    
    if soup.find('div', class_='article-formatted-body article-formatted-body_version-1'):
        text = soup.find('div', class_='article-formatted-body article-formatted-body_version-1').text
    elif soup.find('div', class_='article-formatted-body article-formatted-body_version-2'):
        text = soup.find('div', class_='article-formatted-body article-formatted-body_version-2').text
    print(text)
    print('')

2021-08-09
Танцующие горы Ирана по данным спутниковой интерферометрии
Территория северо-западного Ирана на границе с Каспийским морем выделяется своей сейсмической необузданностью, как во времена молодости нашей планеты. В недрах этого района и сегодня продолжаются процессы нефтегазообразования, например, поблизости от вулкана Дамаванд, геологическую модель которого я показывал ранее. Недавно я занимался вопросом устойчивости плотины Ямчи в провинции Ардебиль и полученные результаты оказались настолько удивительными, что я хочу ими здесь поделиться. Пусть в предыдущих статьях я уже показывал, как растут горы, но чтобы горы еще и танцевали — это мало где удастся увидеть! Как обычно, все данные доступны в GitHub репозитории Yamchi Dam, Ardabil, North Iran.

Плотина выделена красным кольцом, далее от нее в направлении к правому верхнему краю картинки течет река, питающая город Ардебиль. Озеро и плотина растут вверх со коростью около 10 см в год, а сам город с такой же скоростью погружаетс

2021-08-09
Важные советы от HR специалиста для тех, кто готовится к собеседованию
Зачастую поиск работы не приносит столько стрессов, как факт конкретного собеседования, уровень напряжения от которого сопоставим с уровнем стресса при увольнении. Делюсь с вами некоторыми важными моментами, которые помогут вам сохранить ваши нервы перед и во время собеседования.  Собеседование — это встреча двух сторон, у каждой и которых есть свои интересы! Само слово состоит из приставки «со», означающей сопричастность, объединение, и слова «беседа», которая предполагает корректное и уважительное общение людей. Именно поэтому не забывайте о том, что вы не подсудимый и никакого оценивания ваших данных и ваших действий в одностороннем порядке не предполагается, а ваша задача не оправдываться. По сути своей собеседование является переговорным процессом. Работодатель заинтересован в вас, а вы заинтересованы в работе. Именно поэтому ваша беседа должна состоять из презентации обеих сторон, обсуждении условий

2021-08-09
Снится ли GGG Тиму Бернерсу-Ли?
   В 2007 году знаменитый автор слова из трёх букв 'W' опубликовал в своем  блоге рассуждения о востребованности слова нового, на сей раз - из трёх  букв 'G'. "Гигантский Глобальный Граф"  - так предполагалось это произносить в полном, необрезанном виде. О чём  шла речь? О том, что слово "граф" больше подходит для обозначения  технологии представления взамосвязанных данных, нежели "паутина", пусть  даже и "семантическая". Термин не прижился. Отчасти, возможно, из-за  некоторой тавтологичности, отчасти же - из-за того, что привычная  "паутина" оказалась милее сердцу обывателя, чем какой-то "граф".    Ну, да ладно, "ГГГ" не всплыло взлетело - не беда, ведь в конце  концов - это лишь один из возможных псевдонимов планетарной  семантической сети. Но что представлялось сиру Тиму в качестве цели для  достижения (с помощью новых-то технологий связывания данных)?.. "Важны не документы, а то, что в них содержится. Очевидная истина." - писал он, - "...к

2021-08-09
Выбор между технологиями FDM и SLA
На рынке доступно бесчисленное множество технологий и материалов для 3D-печати. Возможно, вы слышали о принтерах, строящих дома, или о принтере для печати шоколадом, или, может быть, даже о биопринтере, способном воссоздавать органы. Хотя многие из этих вариантов реальны, некоторые из них являются научной фантастикой, а другие просто причудливы. В связи с этим возникает вопрос для предпринимателей, инвестирующих в свой собственный бизнес, исследователей, внедряющих новые технологии для своих институтов, и инженеров, которым поручено улучшить жизненный цикл разработки продукта: какая технология 3D-печати подходит для меня?Наиболее часто используемыми технологиями 3D-печати являются стереолитография (SLA) и методом послойного наплавления (FDM). Первоначально представленные в 1980-х годах, эти новаторские технологии адаптировались к современным реалиям благодаря использованию улучшенных материалов, увеличению скорости, размеров и качества. Важ

2021-08-09
PhpStorm 2021.2: дженерики, перечисления, array shapes, новые инспекции и рефакторинги


Вышел второй мажорный релиз PhpStorm в этом году. Под катом подробный разбор всех изменений и новых возможностей с кучей гифок.

Скачать PhpStorm можно на сайте или через приложение Toolbox App.

Как и раньше, для тех, кто занимается опенсорс-проектами, а также для студентов и преподавателей есть бесплатные лицензии. Также предлагаем скидку для стартапов.

PHP


Базовая поддержка дженериков для PHP
Перечисления из PHP 8.1
Однострочные array shapes
Новые инспекции и квик-фиксы
Улучшенное форматирование
Переработанный рефакторинг Extract Method

IDE


Автоматические действия при сохранении кода
Запуск тестов перед коммитом
Автоматическая очистка папок с кэшем и логами
Новый раздел с дополнительными настройками

Контроль версий

Единообразное поведение для Show Diff
Текстовый поиск по локальной истории
Подпись коммитов с помощью GPG

Code With Me


Шэринг экрана

PHP

Поддержка дженериков
Д

...

2021-08-09
Как сделать конфигурационные файлы версионируемыми с инструментами Kubernetes
Привет, Хабр. Меня зовут Валерий Поздяев, я Go-разработчик из команды Billing API SDK в компании Netcracker. Наша команда делает набор инструментов для продукта Cloud Billing. Мы отвечаем за версионирование и лайфсайкл API, настройку и запуск REST/gRPC сервера, аутентификацию и авторизацию, аудит, трассировки и многое другое. Все это на Go.Давайте поговорим про конфиги!Если у ваших приложений есть конфигурационные файлы, то вам должна быть знакома такая ситуация: создаете приложение, создаете конфигурационный файл, документируете его и через какое-то время понимаете, что нужно добавить еще настроек. Старые настройки теперь уже не отвечают всем требованиям, да и в целом структуру лучше поменять.Что делать? Если формат конфигурации никогда не менять, то с годами конфиг-файл превратится в горы “исторически сложилось”. А если его менять... В таком случае вам всегда придется следить за тем, что конфиги 

2021-08-09
Про DevOps для тех, кто изучает Python
Ни за что не поверите, но оказывается IT это не только программисты. Индустрия очень стремительно разрастается и кроме разработчиков существуют project manager’ы, бизнес-аналитики, product owner’ы, scrum-мастера, тестировщики и DevOps’ы. Последние двое тесно связаны с программистами и принимают непосредственное участие в разработке ПО. К тестировщикам мы ещё вернёмся позже, а сегодня же попробуем разобраться, что скрывается за загадочным названием DevOps и как это всё связано с нашим любимым языком программирования Python. Источник: vk.com/pyloungeПредположим программист написал код программы, всё здорово. Однако, просто файлика с исходным кодом недостаточно, чтобы люди могли пользоваться программой. Она должна быть загружена на сервер, этот сервер (возможно облачный) должен быть определённым образом настроен, должна быть установлена база данных, прикручены утилиты и необходимые технологии, которые необходимы нашему файлику с кодом. При

2021-08-09
Реализация CI/CD для корпоративных хранилищ данных
В Сети много рецептов приготовления CI/CD для решения различных проблем и организации процессов под определённые нужды. В этой статье мы опишем ещё один, суть которого - приготовить процесс, максимально близкий к классическому подходу, несмотря на то что предназначен он для разработки КХД, и решить проблему организации работы большой командыЦелиИзбавить разработчиков от бесконечного переноса функционала с одной среды на другую.Создать систему версионирования для решения проблемы зависимости в разработке КХД.Процесс должен соответствовать требованиям ACID, т. е. неисправный патч не должен сломать всё хранилище.Стандартизация разработки. Организация хранилища патчей для Сontinuous Delivery.Организация работы большой команды.Определились с проблемами. Теперь надо найти для них решения.Технологический стекВ итоге была выбрана такая конфигурация:GitLab мы выбрали в качестве репозитория. Oracle - в качестве СУБД, SonarQube - это с

2021-08-09
Как в VSCode смотреть отчёты статических анализаторов, поддерживающих SARIF
В наше время люди всё чаще начинают оптимизировать работу по поиску ошибок в коде, используя статический анализатор. Результаты работы анализатора можно смотреть с помощью разнообразных продуктов. Однако сегодня мы поговорим про просмотр отчёта анализатора в самой стильной среди многофункциональных и самой многофункциональной среди стильных IDE – VSCode. Позволит же нам реализовать нашу задачу формат SARIF и специальный плагин для него. Обо всем этом далее — поехали.Данную статью я написал по просьбе нашего читателя в комментариях к предыдущей статье на тему, связанную с SARIF. Можно сказать, это уже небольшой цикл статей про SARIF :) Поэтому если и вам интересно услышать про то, где и как ещё можно использовать данный формат (или про что угодно), то оставляйте свои пожелания в комментариях.Что такое SARIF?SARIF (Static Analysis Results Interchange Format) – это формат обмена результатами статическог

2021-08-09
Трехлетняя работа в Общественном совете при Казначействе России и новый Профсоюзный общественный совет
Последние 10 лет я занимаюсь открытыми данными, в основном финансовыми, веду общественный проект АНО “Инфокультура” “Госзатраты” (clearspending.ru) и веду телеграм-канал “Ах, Минфин” о том, как публикуются финансовые данные в России и как в них разобраться обычным гражданам. Последние три года я также была членом Общественного совета при Федеральном казначействе (ОС ФК), о котором и пойдет речь в данном посте.На днях был выбран новый состав Общественного совета, поэтому пришло время подвести итоги моей работы в рамках ОС ФК. В первую очередь, хотела бы поблагодарить коллег по Совету и отдельно его председателя, а также сотрудников Федерального казначейства, которые старались сделать Казначейство более открытым, а работу Совета осмысленной и полезной. Сформулирую несколько тезисов о работе в Общественном совете:1. Своей основной задачей при работе в ОС ФК я видела обсуждение

In [ ]:
# запишем данные в датафрейм
habr_news = pd.DataFrame()
def get_all_links(url, query, pages):
    all_refs = []
    params = {
            'search_query': query,
        }
    for i in range(1, pages):
            params['page'] = i
            res = requests.get(url, params)
            #time.sleep(0.3)
            soup = BeautifulSoup(res.text, 'html.parser')
            news_blocks = soup.find_all('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2')
            a_list = list(map(lambda x: x.find('a').get('href'), news_blocks))
            all_refs += list(map(lambda x: 'https://habr.com' + x, a_list))
    return all_refs

    all_links = get_all_links(url, KEYWORDS, 10)

for link in all_links:
    soup = BeautifulSoup(requests.get(link).text, 'html.parser')
    time.sleep(0.2)
    if soup.find('span', class_='tm-article-snippet__datetime-published'):
        date = pd.to_datetime(soup.find('span', class_='tm-article-snippet__datetime-published').find('time').get('datetime'), dayfirst=True).date()
    elif soup.find('div', class_='tm-news-block__meta'):
        date = pd.to_datetime(soup.find('div', class_='tm-news-block__meta').find('time').get('datetime'), dayfirst=True).date()

    if soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2'): 
        title = soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2').text
    elif soup.find('h3', class_='tm-news-block__title'):
        title = soup.find('h3', class_='tm-news-block__title').text
    else:
        title = soup.find('h1', class_='tm-article-snippet__title tm-article-snippet__title_h1').text
    
    if soup.find('div', class_='article-formatted-body article-formatted-body_version-1'):
        text = soup.find('div', class_='article-formatted-body article-formatted-body_version-1').text
    elif soup.find('div', class_='article-formatted-body article-formatted-body_version-2'):
        text = soup.find('div', class_='article-formatted-body article-formatted-body_version-2').text

    row = {'date': date, 'title': title,'all_links': all_links, 'text': text}
    habr_news = pd.concat([habr_news, pd.DataFrame([row])])  
habr_news.reset_index()

In [ ]:
def get_habr_news(links):
    habr_news = pd.DataFrame()
    for link in hubs:
        soup = BeautifulSoup(requests.get(link).text, 'html.parser')
        if soup.find('div', class_='b-article__publish_date'):
            date = pd.to_datetime(soup.find('div', class_='b-article__publish_date').find('time').get('datetime'), dayfirst=True).date()
        elif soup.find('time', class_='title__cake'):
            date = pd.to_datetime(soup.find('time', class_='title__cake').get('datetime'), dayfirst=True).date()
        if soup.find('h2', class_='article_name'): 
            title = soup.find('h2', class_='article_name').text
        else: 
            title = soup.find('h1', class_='article_name').text    
        text = soup.find('div', class_='article_text_wrapper').text
        row = {'date': date, 'title': title, 'text': text}
        habr_news = pd.concat([habr_news, pd.DataFrame([row])])  
    return habr_news
habr_news.reset_index()

# Задание 2. 

Задание 2.
Обязательная часть
Написать скрипт, который будет проверять список e-mail адресов на утечку при помощи сервиса Avast Hack Ckeck. Список email-ов задаем переменной в начале кода:
EMAIL = [xxx@x.ru, yyy@y.com]

В итоге должен формироваться датафрейм со столбцами: <дата утечки> - <источник утечки> - <описание утечки>

Подсказка: сервис работает при помощи "скрытого" API. Внимательно изучите post-запросы.

Дополнительная часть (необязательная)
Написать скрипт, который будет получать 50 последних постов указанной группы во Вконтакте.
Документация к API VK: https://vk.com/dev/methods , вам поможет метод wall.get

GROUP = 'netology'  
TOKEN = УДАЛЯЙТЕ В ВЕРСИИ ДЛЯ ПРОВЕРКИ, НА GITHUB НЕ ВЫКЛАДЫВАТЬ
В итоге должен формироваться датафрейм со столбцами: <дата поста> - <текст поста>



In [ ]:
if soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2'): 
    title = soup.find('h2', class_='tm-article-snippet__title tm-article-snippet__title_h2').text
elif soup.find('h3', class_='tm-news-block__title'):
    title = soup.find('h3', class_='tm-news-block__title').text
elif soup.find('div', class_='tm-promo-block__info'):
    title = soup.find('div', class_='tm-promo-block__info').text    
else:
    title = soup.find('h1', class_='tm-article-snippet__title tm-article-snippet__title_h1').text
print(title)
#<div class="tm-promo-block__info"><h3 class="tm-promo-block__title">Сколько платили айтишникам в первой половине 2021</h3></div>
#<h3 class="tm-promo-block__title">Сколько платили айтишникам в первой половине 2021</h3>
#<h3 class="tm-news-block__title"><a href="/ru/news/t/571978/" class="tm-news-block__title-link tm-news-block__title"><span>Inventive Retail Group приобрела «Румиком», монобрендовый онлайн-магазин Xiaomi</span></a></h3>
#<a href="/ru/post/571596/" class="tm-article-snippet__title-link" data-article-link=""><span>Организуем разметку данных для машинного обучения: методики и инструменты</span></a>
#<h1 lang="ru" class="tm-article-snippet__title tm-article-snippet__title_h1"><span>Способы снизить потребление газа смарт-контрактами</span></h1>
#<h1 lang="ru" class="tm-article-snippet__title tm-article-snippet__title_h1"><span>Способы снизить потребление газа смарт-контрактами</span></h1>